In [1]:
!pip install pandas
!pip install networkx
!pip install networkx_query
!pip install matplotlib

In [1]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt

In [2]:
rides = pd.read_csv('mta_rides.csv')
stations = pd.read_csv('mta_stations.csv')
sample_rides = rides.sample(20000)
top_rides = rides.sample(200)

In [3]:
stations_borough = stations[['Complex ID', 'Borough']]

In [4]:
stations_borough[stations_borough['Complex ID']==611].index


Int64Index([10, 162, 317, 468, 469], dtype='int64')

In [5]:
rides['Origin Station Complex ID'].value_counts()

611    64836
602    56375
610    56142
607    55668
628    54492
       ...  
206     4452
200     4037
201     2905
199     2119
202     1577
Name: Origin Station Complex ID, Length: 424, dtype: int64

In [6]:
stations_borough = stations_borough.drop_duplicates()

In [7]:
stations_borough

Complex ID Borough
0             1       Q
1             2       Q
2             3       Q
3             4       Q
4             5       Q
..          ...     ...
491         517      SI
492         518      SI
493         519      SI
494         522      SI
495         523      SI

[445 rows x 2 columns]

In [8]:
origin_borough_rides = pd.merge(stations_borough, rides, left_on='Complex ID', right_on='Origin Station Complex ID', how='right')

In [9]:
rides_complete = origin_borough_rides.rename(columns={'Borough':'Origin Borough'})

In [10]:
rides_complete = pd.merge(rides_complete, stations_borough, left_on='Destination Station Complex ID', right_on='Complex ID', how='left')

In [11]:
rides_complete = rides_complete.rename(columns={'Borough': 'Destination Borough'})

In [12]:
rides_complete = rides_complete.drop(columns = ['Complex ID_x', 'Complex ID_y', 'Year', 'Month', 'Timestamp', 'Origin Latitude', 'Origin Longitude', 'Destination Latitude', 'Destination Longitude', 'Origin Point', 'Destination Point'])

In [13]:
G = nx.MultiDiGraph()
# for i, j in zip(top_rides['Origin Station Complex ID'], top_rides['Origin Station Complex Name']):
#     G.add_node(i, name=j)
    
for i, j, k in zip(rides_complete['Origin Station Complex ID'], rides_complete['Origin Station Complex Name'], rides_complete['Origin Borough']):
    G.add_node(i, name=j, borough=k)

for i, j, k in zip(rides_complete['Destination Station Complex ID'], rides_complete['Destination Station Complex Name'], rides_complete['Destination Borough']):
    G.add_node(i, name=j, borough=k)
    
origin = list(rides_complete['Origin Station Complex ID'])
dest = list(rides_complete['Destination Station Complex ID'])
ridership = list(rides_complete['Estimated Average Ridership'])
dow = list(rides_complete['Day of Week'])
hod = list(rides_complete['Hour of Day'])

for i, j, k, l, m in zip(origin, dest, ridership, dow, hod):
    G.add_edge(i, j, ridership=k, day=l, hour=m)

In [14]:
ccheck = []
for node in G.nodes:
    ccheck += [node]
    print(G.nodes[node])

{'name': 'DeKalb Av (B,Q,R)', 'borough': 'Bk'}
{'name': 'Grand St (B,D)', 'borough': 'M'}
{'name': '72 St (1,2,3)', 'borough': 'M'}
{'name': '23 St (1)', 'borough': 'M'}
{'name': '68 St-Hunter College (6)', 'borough': 'M'}
{'name': '14 St (F,M,1,2,3)/6 Av (L)', 'borough': 'M'}
{'name': 'Delancey St (F)/Essex St (J,M,Z)', 'borough': 'M'}
{'name': 'Franklin Av (2,3,4,5)/Botanic Garden (S)', 'borough': 'Bk'}
{'name': 'Church Av (F,G)', 'borough': 'Bk'}
{'name': 'Pelham Pkwy (2,5)', 'borough': 'Bx'}
{'name': 'Lorimer St (L)/Metropolitan Av (G)', 'borough': 'Bk'}
{'name': '170 St (B,D)', 'borough': 'Bx'}
{'name': 'Grand Av-Newtown (M,R)', 'borough': 'Q'}
{'name': '28 St (1)', 'borough': 'M'}
{'name': '18 St (1)', 'borough': 'M'}
{'name': 'Canal St (1)', 'borough': 'M'}
{'name': 'Nevins St (2,3,4,5)', 'borough': 'Bk'}
{'name': '23 St (6)', 'borough': 'M'}
{'name': 'Queensboro Plaza (7,N,W)', 'borough': 'Q'}
{'name': 'Vernon Blvd-Jackson Av (7)', 'borough': 'Q'}
{'name': 'Grand Central-42 St 

In [17]:
G.adj[26]

AdjacencyView({355: {0: {'ridership': 0.5556, 'day': 'Monday', 'hour': 1}, 1: {'ridership': 1.4878, 'day': 'Monday', 'hour': 13}, 2: {'ridership': 1.2784, 'day': 'Monday', 'hour': 14}, 3: {'ridership': 2.1476, 'day': 'Monday', 'hour': 15}, 4: {'ridership': 2.8818, 'day': 'Monday', 'hour': 16}, 5: {'ridership': 0.2428, 'day': 'Monday', 'hour': 5}, 6: {'ridership': 2.2306, 'day': 'Monday', 'hour': 17}, 7: {'ridership': 2.663, 'day': 'Monday', 'hour': 18}, 8: {'ridership': 0.482, 'day': 'Monday', 'hour': 7}, 9: {'ridership': 1.4858, 'day': 'Monday', 'hour': 19}, 10: {'ridership': 0.6766, 'day': 'Monday', 'hour': 8}, 11: {'ridership': 1.2282, 'day': 'Monday', 'hour': 20}, 12: {'ridership': 0.745, 'day': 'Monday', 'hour': 9}, 13: {'ridership': 0.969, 'day': 'Monday', 'hour': 21}, 14: {'ridership': 1.2574, 'day': 'Monday', 'hour': 10}, 15: {'ridership': 0.4534, 'day': 'Monday', 'hour': 22}, 16: {'ridership': 1.2204, 'day': 'Monday', 'hour': 11}, 17: {'ridership': 0.9054, 'day': 'Monday', 'ho

In [16]:
G.nodes

NodeView((26, 231, 313, 320, 399, 601, 625, 626, 243, 424, 629, 217, 265, 319, 321, 325, 337, 405, 461, 464, 610, 619, 622, 138, 630, 54, 434, 160, 176, 225, 341, 397, 628, 635, 28, 292, 450, 173, 607, 126, 608, 609, 273, 420, 268, 380, 22, 234, 395, 426, 611, 10, 365, 223, 236, 456, 602, 318, 153, 266, 627, 127, 167, 286, 301, 398, 476, 606, 387, 164, 336, 403, 433, 271, 89, 99, 417, 228, 324, 471, 307, 617, 614, 1, 238, 310, 154, 71, 119, 289, 343, 439, 316, 328, 438, 624, 308, 180, 261, 615, 237, 30, 210, 312, 279, 283, 449, 162, 158, 168, 288, 8, 49, 199, 62, 17, 165, 432, 135, 175, 107, 287, 83, 612, 147, 159, 129, 232, 409, 151, 360, 13, 259, 603, 613, 276, 356, 16, 31, 35, 141, 169, 278, 386, 636, 149, 45, 114, 621, 9, 36, 277, 314, 41, 44, 120, 177, 300, 152, 414, 97, 144, 605, 179, 284, 604, 618, 359, 392, 616, 109, 396, 339, 3, 334, 46, 198, 448, 58, 290, 303, 384, 309, 304, 122, 125, 383, 4, 344, 369, 440, 14, 295, 404, 447, 260, 131, 96, 431, 394, 50, 124, 329, 270, 55, 299

In [21]:
for i in G.adj[231]:
    print(i)

284
265
395
475
606
264
464
303
609
277
625
626
477
141
602
234
319
604
220
32
262
623
297
36
2
618
321
213
413
176
55
47
311
159
1
35
340
65
437
394
3
318
153
232
291
165
343
354
635
476
290
613
146
392
147
177
34
615
388
64
69
150
353
175
58
44
627
337
607
328
195
458
258
305
151
309
323
355
71
160
39
617
614
396
616
316
381
72
383
164
304
341
122
403
10
308
217
359
399
77
162
181
310
33
336
52
611
456
630
612
167
255
51
155
276
307
168
212
66
610
152
313
608
432
158
306
447
439
605
119
601
339
345
450
300
26
211
67
42
382
238
440
38
409
292
619
9
636
240
241
283
261
191
257
53
249
110
5
17
344
346
391
298
460
56
216
43
143
13
94
441
352
221
301
188
393
471
243
48
169
4
245
235
459
228
60
30
449
144
250
154
279
295
225
49
452
434
236
621
68
288
271
120
70
173
109
369
356
14
457
210
50
622
54
289
179
420
251
37
145
357
223
59
445
620
28
428
209
358
8
244
192
268
57
259
348
157
22
443
398
99
451
404
347
377
270
422
278
386
101
41
294
461
266
254
438
387
455
84
405
90
248
118
423
253
21

In [27]:
for i in range(17):
    print(G.edges[(231, 284, i)])


{'ridership': 0.3068, 'day': 'Monday', 'hour': 1}
{'ridership': 0.5308, 'day': 'Monday', 'hour': 13}
{'ridership': 0.7802, 'day': 'Monday', 'hour': 14}
{'ridership': 0.249, 'day': 'Monday', 'hour': 15}
{'ridership': 0.7648, 'day': 'Monday', 'hour': 16}
{'ridership': 0.2526, 'day': 'Monday', 'hour': 17}
{'ridership': 0.4812, 'day': 'Monday', 'hour': 18}
{'ridership': 0.5086, 'day': 'Monday', 'hour': 19}
{'ridership': 0.2488, 'day': 'Monday', 'hour': 8}
{'ridership': 0.2342, 'day': 'Monday', 'hour': 20}
{'ridership': 0.2358, 'day': 'Monday', 'hour': 9}
{'ridership': 0.2424, 'day': 'Monday', 'hour': 21}
{'ridership': 0.255, 'day': 'Monday', 'hour': 10}
{'ridership': 0.5106, 'day': 'Monday', 'hour': 11}
{'ridership': 0.2668, 'day': 'Monday', 'hour': 12}
{'ridership': 0.2674, 'day': 'Tuesday', 'hour': 13}
{'ridership': 0.535, 'day': 'Tuesday', 'hour': 14}


In [28]:
G.number_of_edges(231, 284)

75

In [31]:
for node in G.nodes:
    print(G.nodes[node]['borough'])

Bk
M
M
M
M
M
M
Bk
Bk
Bx
Bk
Bx
Q
M
M
M
Bk
M
Q
Q
M
M
M
Bk
Bk
Bk
Bx
M
Bk
M
Bk
M
M
M
Bk
Bk
Q
Bk
M
Bk
Bk
M
Q
Bx
Q
Bx
M
M
M
Bx
M
M
Bx
M
Bk
Q
M
M
M
Q
Bk
Bk
M
Bk
M
M
M
Q
Bx
M
Bk
M
Bx
Q
Bk
Bk
Bx
M
M
M
M
Bk
M
Q
Bk
M
M
Bk
M
Bk
Bk
M
M
M
M
M
M
Bk
Q
Bk
Bk
Bk
Bx
M
Q
Bk
Q
M
M
M
Bk
M
Bk
Q
Bk
M
M
Bx
Bk
Bk
M
Bk
Q
M
M
M
Q
M
M
M
Bx
M
Q
Bx
M
M
Bk
M
Bk
Bk
Bk
M
Q
Bx
Bk
M
Bk
Bk
Bk
M
Bk
M
M
Bk
Bk
Bk
Bk
M
M
M
Bk
M
M
Bk
Bk
Bx
M
Bk
M
Q
Q
M
Bk
Q
Bk
Bk
Q
Q
Bk
Bk
M
Bx
M
M
Bk
Bk
Bx
Q
Bk
Bx
M
M
Bx
M
Q
Q
Bk
Bk
Bx
M
Bk
Bk
M
Q
Bk
M
M
Bk
M
Bx
Bx
M
Bk
M
Bx
M
Q
M
Bk
M
Bk
Bk
Bx
Q
M
M
Bk
Q
Bk
M
M
Bx
Bk
Bx
Bk
Bk
Q
Bx
Q
M
Bx
Bx
Bk
Bx
Bk
Bk
Bx
M
Q
Q
Bx
Bk
M
Bk
M
Bx
Bk
Bx
Bx
Bx
Bx
Bk
Bk
Q
Bk
Bk
Bk
M
Q
M
Q
Bk
Bk
Q
Bx
Bx
Bk
Q
Q
M
Q
Bx
Q
Bk
M
Bk
Bk
Bk
Bk
Bk
M
Bx
M
Bk
Bk
Q
Bk
Q
Q
Bk
Bx
Bk
M
Q
Bk
Bk
Bk
Q
Bk
Bk
Q
Bk
Bk
M
Bx
Q
Q
Bx
M
Bx
Bk
Bk
Bx
Bk
Bk
Q
Bk
M
Bk
Bk
Bk
Bk
Bk
Bx
Bx
Bk
Bk
Bx
M
Bk
M
Bk
Bx
Q
Q
Bk
Q
Bk
Q
Bx
Bk
Q
Q
Bk
Bx
M
M
Bk
Q
Bk
Bk
Bx
Q
Bk
Bk
Q
Bk
Bx
Bk
Bx
M
Q
Bk
Bx
Bk
Bk
Bx
Q
Bk
Q
Bk
Bk
Bx
Bk
Bx
Bk
Q
Q
Bx
Bk
Bk
Bk
Bx
Bk
Bk


In [64]:
set([i[1]['borough'] for i in G.nodes(data=True)])

{'Bk', 'Bx', 'M', 'Q'}

In [70]:
set([i for i in G.out_edges(231)])

{(231, 1),
 (231, 2),
 (231, 3),
 (231, 4),
 (231, 5),
 (231, 6),
 (231, 8),
 (231, 9),
 (231, 10),
 (231, 13),
 (231, 14),
 (231, 16),
 (231, 17),
 (231, 20),
 (231, 22),
 (231, 26),
 (231, 28),
 (231, 30),
 (231, 31),
 (231, 32),
 (231, 33),
 (231, 34),
 (231, 35),
 (231, 36),
 (231, 37),
 (231, 38),
 (231, 39),
 (231, 41),
 (231, 42),
 (231, 43),
 (231, 44),
 (231, 45),
 (231, 46),
 (231, 47),
 (231, 48),
 (231, 49),
 (231, 50),
 (231, 51),
 (231, 52),
 (231, 53),
 (231, 54),
 (231, 55),
 (231, 56),
 (231, 57),
 (231, 58),
 (231, 59),
 (231, 60),
 (231, 61),
 (231, 62),
 (231, 64),
 (231, 65),
 (231, 66),
 (231, 67),
 (231, 68),
 (231, 69),
 (231, 70),
 (231, 71),
 (231, 72),
 (231, 74),
 (231, 75),
 (231, 76),
 (231, 77),
 (231, 78),
 (231, 79),
 (231, 80),
 (231, 81),
 (231, 82),
 (231, 83),
 (231, 84),
 (231, 85),
 (231, 86),
 (231, 87),
 (231, 88),
 (231, 89),
 (231, 90),
 (231, 91),
 (231, 93),
 (231, 94),
 (231, 95),
 (231, 96),
 (231, 97),
 (231, 98),
 (231, 99),
 (231, 100),

In [35]:
# list of all boroughs in data
borough_list = set([i[1]['borough'] for i in G.nodes(data=True)])

# all station complex IDs in borough M
manhattan_stations_id = [node for node in G.nodes if G.nodes[node]['borough'] == 'M']

# all edges out of node 231
[G.edges(i) for i in G.out_edges(231)]

# sum of total ridership from node 231 to 284 for all days and hours
wow = sum([G.get_edge_data(231, 284, i)['ridership'] for i in G.get_edge_data(231, 284)])


In [82]:
# Question 1.a)
# Finding list of all boroughs
borough_list = set([i[1]['borough'] for i in G.nodes(data=True)])
# List of most busy origin stations in each borough
borough_top = []
# Iterating through each borough
for borough in borough_list:
    # List of all stations in borough
    stations_id = [node for node in G.nodes if G.nodes[node]['borough'] == borough]
    # List of stations and their total ridership
    station_ridership_list = []
    # Iterating through each station
    for station in stations_id:
        # List of all unique ride pairs where station is origin
        origin_rides = set([i for i in G.out_edges(station)])
        # Total ridership of station
        total_ridership = 0
        for ride in origin_rides:
            total_ridership += sum([G.get_edge_data(ride[0], ride[1], i)['ridership'] for i in G.get_edge_data(ride[0], ride[1])])
        station_ridership_list += [(total_ridership, station)]
    borough_top += [G.nodes[max(station_ridership_list)[1]]['name']]

borough_top

(424, 49)
(424, 58)
(424, 296)
(424, 67)
(424, 305)
(424, 314)
(424, 323)
(424, 179)
(424, 417)
(424, 188)
(424, 426)
(424, 197)
(424, 444)
(424, 453)
(424, 26)
(424, 35)
(424, 44)
(424, 282)
(424, 53)
(424, 291)
(424, 62)
(424, 300)
(424, 309)
(424, 318)
(424, 147)
(424, 156)
(424, 165)
(424, 183)
(424, 421)
(424, 430)
(424, 439)
(424, 448)
(424, 30)
(424, 39)
(424, 277)
(424, 48)
(424, 286)
(424, 295)
(424, 304)
(424, 313)
(424, 151)
(424, 160)
(424, 398)
(424, 169)
(424, 407)
(424, 416)
(424, 425)
(424, 434)
(424, 16)
(424, 263)
(424, 34)
(424, 272)
(424, 43)
(424, 290)
(424, 299)
(424, 137)
(424, 146)
(424, 155)
(424, 393)
(424, 164)
(424, 420)
(424, 429)
(424, 2)
(424, 20)
(424, 258)
(424, 276)
(424, 294)
(424, 123)
(424, 141)
(424, 379)
(424, 150)
(424, 388)
(424, 159)
(424, 397)
(424, 6)
(424, 244)
(424, 253)
(424, 262)
(424, 271)
(424, 280)
(424, 109)
(424, 118)
(424, 127)
(424, 136)
(424, 374)
(424, 145)
(424, 383)
(424, 392)
(424, 630)
(424, 1)
(424, 10)
(424, 31)
(424, 248)


In [83]:
borough_top

['161 St-Yankee Stadium (B,D,4)',
 'Atlantic Av-Barclays Ctr (B,D,N,Q,R,2,3,4,5)',
 '74-Broadway (7)/Jackson Hts-Roosevelt Av (E,F,M,R)',
 'Times Sq-42 St (N,Q,R,W,S,1,2,3,7)/42 St (A,C,E)']